In [5]:
import pandas as pd
# import openslide
import os
import glob
import os

In [6]:

# directory = "/home/sam/Desktop/astar/TCGA_test/0166427c-15c9-4b49-954c-eb3545e5699e"

# # "TCGA-G3-A7M6-01Z-00-DX1.550E0F12-BF91-45B1-9FD7-1FEB1F9E9A12.svs"
# len(list(os.walk(directory)))

# print(list(os.walk(directory)))


# # glob.glob("/home/sam/Desktop/astar/TCGA_data",*, recursive=False)

In [2]:
# create a mapping from the tiled image to the non-tiled image , 

import os
orig_window = 296


def tile_images(img_dir, i, orig_window):
    data_list = [] 
    data_dict = {}
    new_dir = os.path.join(os.path.abspath(os.path.join(img_dir, os.pardir)),f"HE_BC{30000+i}/")
    os.rename(img_dir, new_dir)
    for img in os.listdir(new_dir):
        print(img)
        if img.endswith(".tif"):
            info = img.split("_")
            coord_info = info[3].split("-")
            col = int(coord_info[0])//orig_window
            row = int(coord_info[1])//orig_window
            # BC30001_99_59.tif

            data_dict = {"label": f"BC{30000+i}", "x_coords" : col, "y_coords" : row, "x_pixel_coords" : coord_info[0], "y_pixel_coords" : coord_info[1]}
            data_list.append(data_dict)
            print(os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
            os.rename(os.path.join(new_dir, img), os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
        

# "/home/sam/Desktop/astar/TCGA_test/CD74_tiled"
# tile_images("./processed/grid/", 5, 296)

In [9]:
# "/home/sam/Desktop/astar/TCGA_test/tiled_data/HE_BC30004_C1/labels.csv" 


import pandas as pd 
import numpy as np
def read_csv_tsv(fp, dtype = None):
    if fp.endswith(".csv"):
        df = pd.read_csv(fp, dtype=dtype)
    elif fp.endswith(".tsv"):
        df = pd.read_table(fp, dtype=dtype)
    return df

def save_tsv_csv(fp, df):
    if fp.endswith(".csv.gz"):
        df.to_csv(fp, index= False, compression={'method': 'gzip'})
    elif fp.endswith(".tsv.gz"):
        df.to_csv(fp, sep = "\t", index=False, compression={'method': 'gzip'})
    return df


def read_csv_to_list(filename):
    df = pd.read_csv(filename)
    return df.to_dict('records')

def stdata_map(input_file, output_file, input_list, i, fill_val = int(1)):
    df = read_csv_tsv(input_file)
    coords = []
    print(input)
    for dic in input_list:
        x_coords = dic["x_coords"]
        y_coords = dic["y_coords"]
        vals = f"{x_coords}x{y_coords}"
        coords.append(vals)       
    print("why so")
    df_series = pd.Series(coords, name = "Unnamed: 0")    
    zero_data = np.full(fill_value = 1, shape=(len(coords),len(df.columns[1:])), dtype = 'int8')
#     np.random.randint(1, 5, shape=(len(coords),len(df.columns[1:])), dtype = "int8")
    df_vals = pd.DataFrame(zero_data, columns=df.columns[1:], dtype = "int8" )
    print(df_vals) 
    print("Slow")
    df = pd.concat([df_series, df_vals], axis=1)
    print(df)
    print("stdata_map saved")
    save_tsv_csv(output_file, df)
    
def spots_map(input_file, output_file, input_list):
#     fill_val = 1
    df = read_csv_tsv(input_file)
#         df = pd.DataFrame(data)
    coords, x_pixel, y_pixel = [], [], []
    for dic in input_list:
        x_coords = dic["x_coords"]
        y_coords = dic["y_coords"]
        x_pixel_coords = dic["x_pixel_coords"]
        y_pixel_coords = dic["y_pixel_coords"]
        vals = f"{x_coords}x{y_coords}"
        coords.append(vals)
        x_pixel.append(x_pixel_coords)
        y_pixel.append(y_pixel_coords)
    df_vals = pd.DataFrame({"Unnamed: 0":coords, "X":x_pixel, "Y":y_pixel}, columns=df.columns)                             
    df = pd.concat([df, df_vals])
    save_tsv_csv(output_file, df)
    print("spots_map saved")
    

def coords_map(input_file, output_file, input_list):
    i= 0 
    df = read_csv_tsv(input_file)
    coords, x_pixel, y_pixel, labs, tumors = [], [], [], [], []
    for dic in input_list:
        x_coords = dic["x_coords"]
        y_coords = dic["y_coords"]
        lab = f"L{i}"
        tumor = "non"
        i+= 1
        vals = f"C1_{x_coords}.0_{y_coords}.0"
        coords.append(vals)
        x_pixel.append(x_coords)
        y_pixel.append(y_coords)
        labs.append(lab)
        tumors.append(tumor)
        
    df_vals = pd.DataFrame({"xcoord":coords, "ycoord":x_pixel, "lab":y_pixel, "tumor":labs , "Unnamed: 4": tumors}, columns=df.columns)
                             
    df = pd.concat([df, df_vals], ignore_index= True)
    save_tsv_csv(output_file, df)
    print("coords_map saved")
    
def meta_map(input_file,output_file, name):
    df = read_csv_tsv(input_file)
#     df.append(data, ignore_index=true)
    ref_row = df.iloc[0,:]
    ref_row_mod = ref_row.str.replace("BC30001", name, regex = True )
    ref_row_df = pd.DataFrame(ref_row_mod).T
    df_modified = pd.concat([df, ref_row_df], ignore_index=True, axis = 0)
#     save_tsv_csv(output_file, df)
    df_modified.to_csv(output_file, index= False)
    print("meta_map saved")


def make_dummy_data(output_dir, base_dir, dummy_dir):
    """
    output_dir: filepath to which dummy data will be sent
    base_dir: directory where different representative label files are
    dummy_dir, where there are dummy files
    """
    os.makedirs(output_dir, exist_ok = True)

    for fname in sorted(os.listdir(base_dir)):
        if fname.endswith(".csv"):
            filename = os.path.join(base_dir, fname)
            actual_labels = read_csv_to_list(filename)
            i = int(fname.split("_")[0][2:])-30000 
            stdata_map(os.path.join(dummy_dir,f"BC{30005}_C1_stdata.tsv"), os.path.join(output_dir, f"BC{30000+i}_C1_stdata.tsv.gz"), actual_labels,i)
            spots_map(os.path.join(dummy_dir, f"spots_BC{30005}_C1.csv"), os.path.join(output_dir,f"spots_BC{30000+i}_C1.csv.gz"), actual_labels)
            coords_map(os.path.join(dummy_dir, f"BC{30005}_C1_Coords.tsv"), os.path.join(output_dir, f"BC{30000+i}_C1_Coords.tsv.gz"), actual_labels)
            if i == 20:
                input_dir = os.path.join(dummy_dir,"metadata.csv")
            else:
                input_dir = os.path.join(output_dir,"metadata.csv")

            meta_map(input_dir, os.path.join(info_dir,"metadata.csv"), f"BC{30000+i}")
            print(f"BC{30000+i}", "saved")

for gene in ["ALB", "CD74"]:
    base_dir = f"./{gene}_labels"
    dummy_dir = "./dummy"
    output_dir = "."

    make_dummy_data(output_dir, base_dir, dummy_dir)

        
# filename = "/home/sam/Desktop/astar/TCGA_test/tiled_data/labels.csv"  # Replace with your CSV filename

<bound method Kernel.raw_input of <ipykernel.ipkernel.IPythonKernel object at 0x7f1b01fcf9d0>>
why so
      ENSG00000243485  ENSG00000237613  ENSG00000186092  ENSG00000238009  \
0                   1                1                1                1   
1                   1                1                1                1   
2                   1                1                1                1   
3                   1                1                1                1   
4                   1                1                1                1   
...               ...              ...              ...              ...   
2331                1                1                1                1   
2332                1                1                1                1   
2333                1                1                1                1   
2334                1                1                1                1   
2335                1                1                1       

spots_map saved
coords_map saved
meta_map saved
BC30020 saved
<bound method Kernel.raw_input of <ipykernel.ipkernel.IPythonKernel object at 0x7f1b01fcf9d0>>
why so
      ENSG00000243485  ENSG00000237613  ENSG00000186092  ENSG00000238009  \
0                   1                1                1                1   
1                   1                1                1                1   
2                   1                1                1                1   
3                   1                1                1                1   
4                   1                1                1                1   
...               ...              ...              ...              ...   
3398                1                1                1                1   
3399                1                1                1                1   
3400                1                1                1                1   
3401                1                1                1                1   


KeyboardInterrupt: 

In [2]:
import os
base_dir = "/home/sam/Desktop/astar/TCGA_test/ALB_norm_new"
for fname in sorted(os.listdir(base_dir)):
    if fname.endswith(".csv"):
        print(fname)

BC30010_labels.csv
BC30011_labels.csv
BC30012_labels.csv
BC30013_labels.csv
BC30014_labels.csv
BC30015_labels.csv
BC30020_labels.csv
BC30021_labels.csv
BC30022_labels.csv
BC30023_labels.csv
BC30024_labels.csv
BC30025_labels.csv
BC30030_labels.csv
BC30031_labels.csv
BC30032_labels.csv
BC30033_labels.csv
BC30034_labels.csv
BC30035_labels.csv


In [ ]:
from sklearn.model_selection import train_test_split

dX_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.33, random_state=42)


In [65]:
# !pip list | grep pandas

pandas                            1.5.3


### Train test split

In [ ]:
# !ls ../data/hist2tscript/


In [ ]:
# !gunzip -k ../data/hist2tscript/BC30001_C1_Coords.tsv.gz | echo y
# !gunzip -k ../data/hist2tscript/spots_BC30001_C1.csv.gz |echo y
# !gunzip -k ../data/hist2tscript/BC30001_C1_stdata.tsv.gz | echo y

cat: ../data/hist2script/BC30001_C1_Coords.tsv: No such file or directory


In [3]:
# BC30001_C1_Coords.tsv
# spots_BC30001_C1.csv
# !gunzip -k "./data/hist2script/BC30001_C1_Coords.tsv"
# !gunzip -k "./data/hist2script/spots_BC30001_C1.csv
# !gunzip -k "./data/hist2script/BC30001_C1_stdata.tsv

data_dir = "../data/hist2tscript"


import pandas as pd
import shutil
import os

def read_csv_tsv(fp, dtype = None):
    if fp.endswith(".csv"):
        df = pd.read_csv(fp, dtype=dtype)
    elif fp.endswith(".tsv"):
        df = pd.read_table(fp, dtype=dtype)
    return df

def save_tsv_csv(fp, df):
    if fp.endswith(".csv.gz"):
        df.to_csv(fp, index= False, compression={'method': 'gzip'})
    elif fp.endswith(".tsv.gz"):
        df.to_csv(fp, sep = "\t", index=False, compression={'method': 'gzip'})
    return df

def read_csv_to_list(filename):
    df = pd.read_csv(filename)
    return df.to_dict('records')
df_coords = read_csv_tsv(os.path.join(data_dir,"BC30001_C1_Coords.tsv"))
df_spots = read_csv_tsv(os.path.join(data_dir, "spots_BC30001_C1.csv"))

def meta_map(input_file,output_file, name):
    df = read_csv_tsv(input_file)
#     df.append(data, ignore_index=true)
    ref_row = df.iloc[0,:]
#     print(type(ref_row))
    ref_row_mod = ref_row.str.replace("BC30001", name, regex = True )
    ref_row_df = pd.DataFrame(ref_row_mod).T

#     print(ref_row_mod)
    df_modified = pd.concat([df, ref_row_df], ignore_index=True, axis = 0)
#     save_tsv_csv(output_file, df)
    df_modified.to_csv(output_file, index= False)
#     print(save_tsv_csv(output_file, df_modified).head)

from sklearn.model_selection import train_test_split

df_spots_train, df_spots_test, df_coords_train, df_coords_test = train_test_split(df_spots, df_coords, test_size=0.2, random_state=42)

# print(df_spots_train, df_spots_test, df_coords_train, df_coords_test)

train_coords = [tuple(i.split('x')) for i in list(df_spots_train["Unnamed: 0"])]
test_coords = [tuple(i.split('x')) for i in list(df_spots_test["Unnamed: 0"])]


# df_stdata  = read_csv_tsv("data_HCC1/BC30001_C1_stdata.tsv").head(5)
# df_stdata = pd.read_table("data_HCC1/BC30001_C1_stdata.tsv",usecols = ["Unnamed: 0","ENSG00000243485"], dtype=None)
df_stdata = pd.read_table(os.path.join(data_dir,"BC30001_C1_stdata.tsv"), dtype=None)

# print(df_stdata)

# stdata_coords = [i.split('x') for i in list(df_stdata["Unnamed: 0"])]
# print(len(stdata_coords))

# stdata_coords = [tuple(i.split('x')) for i in list(df_stdata["Unnamed: 0"])]
# print(len(set(stdata_coords)))
# stdata_coords - train_coords

stdata_train_coords = ["x".join(i) for i in train_coords]
stdata_test_coords = ["x".join(i) for i in test_coords]

# for stdata_coords in 
# print(stdata_coords)
base_dir = os.path.join(data_dir,"HE_BC30001_C1") 
save_dir = os.path.join(base_dir, "..")
train_dir = "HE_BC30006"
test_dir = "HE_BC30007"

train_name = "30006"
test_name = "30007"

os.makedirs(os.path.join(base_dir, "..", train_dir), exist_ok = True)
os.makedirs(os.path.join(base_dir, "..", test_dir), exist_ok = True)

df_stdata_test = df_stdata[df_stdata['Unnamed: 0'].isin(stdata_test_coords)]
df_stdata_train = df_stdata[~(df_stdata['Unnamed: 0'].isin(stdata_test_coords))]

print(df_stdata_test, df_stdata_train)

for fname in os.listdir(base_dir):
    path = os.path.join(base_dir, fname)
    underscore_split = fname.split("_")
    img_coord = (underscore_split[1],underscore_split[-1].split(".")[0])
#     print()
#     print(list(underscore_split[-1].split(".")[0]))
    print(img_coord) 
    if img_coord in test_coords:
        print(os.path.join(base_dir, "..", test_dir))
        shutil.copy(path, os.path.join(base_dir, "..", test_dir))
    elif img_coord in train_coords: 
        print(os.path.join(base_dir, "..", train_dir))
        shutil.copy(path, os.path.join(base_dir, "..", train_dir))

        
# df_spots_train, df_spots_test, df_coords_train, df_coords_test

# df_stdata_test = df_stdata[df_stdata['Unnamed: 0'].isin(stdata_test_coords)]
# df_stdata_train
save_tsv_csv(os.path.join(save_dir, f"BC{train_name}_C1_stdata.tsv.gz"),df_stdata_train)
save_tsv_csv(os.path.join(save_dir,f"spots_BC{train_name}_C1.csv.gz"),df_spots_train)
save_tsv_csv(os.path.join(save_dir, f"BC{train_name}_C1_Coords.tsv.gz"), df_coords_train)

save_tsv_csv(os.path.join(save_dir, f"BC{test_name}_C1_stdata.tsv.gz"), df_stdata_test)
save_tsv_csv(os.path.join(save_dir,f"spots_BC{test_name}_C1.csv.gz"), df_spots_test)
save_tsv_csv(os.path.join(save_dir, f"BC{test_name}_C1_Coords.tsv.gz"), df_coords_test)

# meta_map(os.path.join(f"./dummy","metadata.csv"), os.path.join(save_dir,"metadata.csv"), f"BC{train_name}")
# meta_map(os.path.join(save_dir,"metadata.csv"), os.path.join(save_dir,"metadata.csv"), f"BC{test_name}")


# shutil.copy(os.path.join(save_dir, "HE_BC30001_C1.tif"),os.path.join(save_dir, f"{train_dir}_C1.tif") )
# shutil.copy(os.path.join(save_dir, "HE_BC30001_C1.tif"),os.path.join(save_dir, f"{test_dir}_C1.tif") )


print("done")



     Unnamed: 0  ENSG00000243485  ENSG00000237613  ENSG00000186092  \
4         28x42                0                0                0   
6         83x65                0                0                0   
8          64x6                0                0                0   
11        59x67                0                0                0   
12        70x66                0                0                0   
...         ...              ...              ...              ...   
3012       44x8                0                0                0   
3017      82x16                0                0                0   
3029      58x22                0                0                0   
3032      60x18                0                0                0   
3034      60x56                0                0                0   

      ENSG00000238009  ENSG00000239945  ENSG00000239906  ENSG00000241860  \
4                   0                0                0                0   
6      

('BC30001', '42')
('BC30001', '31')
('BC30001', '44')
('BC30001', '57')
('BC30001', '3')
('74', '30')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('39', '45')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('44', '72')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '16')
('BC30001', '47')
('90', '24')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('25', '49')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('22', '42')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '48')
('BC30001', '8')
('BC30001', '52')
('40', '34')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('105', '45')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '43')
('BC30001', '14')
('79', '39')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('81', '21')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('33', '47')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('51', '31')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('114', '40')
../data/hist2tscript/HE_BC3

('45', '69')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('72', '20')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '15')
('43', '9')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '47')
('BC30001', '45')
('20', '14')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '21')
('BC30001', '24')
('71', '11')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('46', '58')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('103', '29')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '66')
('BC30001', '35')
('41', '53')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('104', '22')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('96', '48')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '10')
('23', '25')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('59', '19')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('91', '43')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('60', '14')
../data/hist2tscript/HE_BC30001_C1/.

('BC30001', '13')
('20', '26')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '36')
('BC30001', '65')
('107', '21')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('42', '50')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('75', '19')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '27')
('72', '12')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('36', '28')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('83', '45')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '4')
('31', '23')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '16')
('53', '55')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '33')
('BC30001', '60')
('BC30001', '29')
('22', '6')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '9')
('63', '17')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '38')
('BC30001', '22')
('106', '48')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('74', '70')
../data/hist2tscript/HE_BC30

('BC30001', '13')
('BC30001', '66')
('76', '26')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '18')
('BC30001', '51')
('89', '35')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('46', '64')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '23')
('92', '32')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('55', '9')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('20', '54')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('95', '39')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '28')
('BC30001', '61')
('42', '22')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('107', '53')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '17')
('BC30001', '44')
('72', '60')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('45', '29')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('100', '58')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '55')
('83', '37')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '

...

('58', '4')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('55', '65')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '19')
('BC30001', '50')
('37', '13')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '53')
('BC30001', '26')
('BC30001', '40')
('30', '18')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '11')
('BC30001', '61')
('BC30001', '28')
('BC30001', '32')
('BC30001', '14')
('56', '54')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('113', '25')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '3')
('BC30001', '23')
('BC30001', '56')
('BC30001', '39')
('66', '16')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('86', '44')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('33', '29')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('49', '15')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '17')
('34', '22')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('79', '57')
../data/hist2tscript/HE_BC30001_C1/.

('BC30001', '48')
('BC30001', '7')
('16', '42')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '53')
('BC30001', '58')
('12', '8')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '40')
('BC30001', '35')
('BC30001', '47')
('BC30001', '39')
('105', '41')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('40', '30')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('22', '46')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('90', '20')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('68', '38')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '15')
('BC30001', '58')
('BC30001', '42')
('114', '44')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('51', '35')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '53')
('BC30001', '49')
('33', '43')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('34', '48')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('81', '25')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('59', '13')
../data/h

('BC30001', '66')
('57', '25')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '59')
('BC30001', '10')
('BC30001', '43')
('67', '67')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '52')
('BC30001', '27')
('BC30001', '48')
('BC30001', '20')
('31', '15')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('109', '53')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '46')
('BC30001', '14')
('63', '21')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('54', '68')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '56')
('38', '2')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('53', '63')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '48')
('20', '10')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '25')
('BC30001', '19')
('BC30001', '43')
('BC30001', '41')
('72', '24')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('BC30001', '11')
('BC30001', '58')
('42', '66')
../data/hist2tscript/HE_BC30001_C1/../HE_BC

('54', '26')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '40')
('BC30001', '13')
('36', '50')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '10')
('BC30001', '65')
('BC30001', '52')
('84', '36')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30007
('93', '51')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('21', '37')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '9')
('106', '30')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('43', '41')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '36')
('82', '54')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '61')
('37', '39')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('30', '32')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '22')
('BC30001', '38')
('BC30001', '71')
('52', '44')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('73', '9')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '29')
('BC30001', '6')
('BC30001', '33')
('81',

('BC30001', '28')
('BC30001', '61')
('BC30001', '32')
('54', '54')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '30')
('19', '21')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('111', '25')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '17')
('BC30001', '62')
('36', '22')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('84', '44')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '20')
('31', '29')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('57', '65')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '25')
('98', '34')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '50')
('BC30001', '19')
('67', '27')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '12')
('48', '24')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('32', '18')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('BC30001', '40')
('31', '9')
../data/hist2tscript/HE_BC30001_C1/../HE_BC30006
('78', '66')
../data/hist2tscript/HE_BC3

In [12]:

# i = 5

# stdata_map(f"./dummy/BC{30000+i}_C1_stdata.tsv", f"./dummy/BC{30000+i}_C1_stdata_ft.tsv", 5, actual_labels)



In [9]:
# dummy_labels = [{"label": "BC30005", "x_coords" : 0, "y_coords" : 0, "x_pixel_coords" : 128, "y_pixel_coords" : 128},
#                 {"label": "BC30005", "x_coords" : 0, "y_coords" : 1, "x_pixel_coords" : 128, "y_pixel_coords" : 384}]


# spots_map(f"./dummy/spots_BC{30000+i}_C1.csv", f"./dummy/spots_BC{30000+i}_C1_ft.csv", actual_labels)
# spots_map("./dummy/spots_BC30005_C1.csv", "./dummy/spots_BC30005_C1_ft.csv", dummy_labels)





<bound method NDFrame.head of      Unnamed: 0      X      Y
0           0x0    148    148
1           1x0    444    148
2           2x0    740    148
3           3x0   1036    148
4           4x0   1332    148
...         ...    ...    ...
8187     123x63  36556  37444
8188     124x63  36852  37444
8189     125x63  37148  37444
8190     126x63  37444  37444
8191     127x63  37740  37444

[8192 rows x 3 columns]>
  Unnamed: 0     X    Y
0        0x0   148  148
1        1x0   444  148
2        2x0   740  148
3        3x0  1036  148
4        4x0  1332  148


In [32]:
print(actual_labels[1])

{'Unnamed: 0': 1, 'label': 'BC30005', 'x_coords': 1, 'y_coords': 0, 'x_pixel_coords': 444, 'y_pixel_coords': 148}


In [33]:
# # dummy_labels = [{"label": "BC30005", "x_coords" : 0, "y_coords" : 0, "x_pixel_coords" : 128, "y_pixel_coords" : 128},
# #                 {"label": "BC30005", "x_coords" : 0, "y_coords" : 1, "x_pixel_coords" : 128, "y_pixel_coords" : 384}]

# # bound method NDFrame.head of             xcoord  ycoord   lab  tumor Unnamed: 4
# # 0     C1_23.0_13.0    23.0  13.0     L0        non
# # 1     C1_25.0_13.0    25.0  13.0     L1        non
# # 2     C1_27.0_13.0    27.0  13.0     L2        non
# # 3     C1_22.0_14.0    22.0  14.0     L3        non
# # 4     C1_24.0_14.0    24.0  14.0     L4        non
# # ...            ...     ...   ...    ...        ...
# # 1412  C1_66.0_68.0    66.0  68.0  L1412        non
# # 1413  C1_68.0_68.0    68.0  68.0  L1413        non
# # 1414  C1_72.0_68.0    72.0  68.0  L1414        non
# # 1415  C1_65.0_69.0    65.0  69.0  L1415        non
# # 1416  C1_67.0_69.0    67.0  69.0  L1416        non
# def coords_map(input_file, output_file, input_list):
#     i= 0 
# #     fill_val = 1
#     df = read_csv_tsv(input_file)
# #         df = pd.DataFrame(data)
#     coords, x_pixel, y_pixel, labs, tumors = [], [], [], [], []
#     for dic in input_list:
#         x_coords = dic["x_coords"]
#         y_coords = dic["y_coords"]
# #         print(x_coords,y_coords)
# #         x_pixel_coords = dic["x_pixel_coords"]
# #         y_pixel_coords = dic["y_pixel_coords"]
#         lab = f"L{i}"
#         tumor = "non"
#         i+= 1
#         vals = f"C1_{x_coords}.0_{y_coords}.0"
#         coords.append(vals)
#         x_pixel.append(x_coords)
#         y_pixel.append(y_coords)
#         labs.append(lab)
#         tumors.append(tumor)
        
    
#     df_vals = pd.DataFrame({"xcoord":coords, "ycoord":x_pixel, "lab":y_pixel, "tumor":labs , "Unnamed: 4": tumors}, columns=df.columns)
# #     df_vals.iloc[:len(coords), ~df.columns.isin(["Unnamed: 0","X", "Y"])] = fill_val
#     print(df_vals.head)
                             
#     df = pd.concat([df, df_vals], ignore_index= True)
# #     df = pd.concat([df, df_vals], ignore_index= True)

#     save_tsv_csv(output_file, df)
#     print(df.head())
# #     df = 

# coords_map(f"./dummy/BC{30000+i}_C1_Coords.tsv", f"./dummy/BC{30000+i}_C1_Coords_ft.tsv", actual_labels)




<bound method NDFrame.head of              xcoord  ycoord  lab  tumor Unnamed: 4
0        C1_0.0_0.0       0    0     L0        non
1        C1_1.0_0.0       1    0     L1        non
2        C1_2.0_0.0       2    0     L2        non
3        C1_3.0_0.0       3    0     L3        non
4        C1_4.0_0.0       4    0     L4        non
...             ...     ...  ...    ...        ...
8187  C1_123.0_63.0     123   63  L8187        non
8188  C1_124.0_63.0     124   63  L8188        non
8189  C1_125.0_63.0     125   63  L8189        non
8190  C1_126.0_63.0     126   63  L8190        non
8191  C1_127.0_63.0     127   63  L8191        non

[8192 rows x 5 columns]>
       xcoord ycoord lab tumor Unnamed: 4
0  C1_0.0_0.0      0   0    L0        non
1  C1_1.0_0.0      1   0    L1        non
2  C1_2.0_0.0      2   0    L2        non
3  C1_3.0_0.0      3   0    L3        non
4  C1_4.0_0.0      4   0    L4        non


In [10]:
# def meta_map(input_file,output_file, name):
# #     data = {"type": "HCC", "patient": patient, "replicate": "C1",
# #            "count_matrix": count, "histology_image": hist, 
# #             "spot_coordinates" : spot, "tumor_annotation" : tumor 
# #            }
    
#     df = read_csv_tsv(input_file)
# #     df.append(data, ignore_index=true)
#     ref_row = df.iloc[0,:]
#     print(type(ref_row))
#     ref_row_mod = ref_row.str.replace("BC30001", name, regex = True )
#     ref_row_df = pd.DataFrame(ref_row_mod).T

#     print(ref_row_mod)
#     df_modified = pd.concat([df, ref_row_df], ignore_index=True, axis = 0)
# #     save_tsv_csv(output_file, df)
#     print(save_tsv_csv(output_file, df_modified).head)

# meta_map("./data/metadata.csv", "./dummy/metadata.csv", f"BC{30000+i}")


#   type  patient replicate              count_matrix    histology_image  \
# 0  HCC  BC30001        C1  BC30001_C1_stdata.tsv.gz  HE_BC30001_C1.tif   
# 1  HCC  BC30002        C1  BC30002_C1_stdata.tsv.gz  HE_BC30002_C1.tif   
# 2  HCC  BC30003        C1  BC30003_C1_stdata.tsv.gz  HE_BC30003_C1.tif   
# 3  HCC  BC30004        C1  BC30004_C1_stdata.tsv.gz  HE_BC30004_C1.tif   
# 4  NCC  BC42334        C1  BC42334_C1_stdata.tsv.gz  HE_BC42334_C1.tif   

#           spot_coordinates          tumor_annotation  
# 0  spots_BC30001_C1.csv.gz  BC30001_C1_Coords.tsv.gz  
# 1  spots_BC30002_C1.csv.gz  BC30002_C1_Coords.tsv.gz  
# 2  spots_BC30003_C1.csv.gz  BC30003_C1_Coords.tsv.gz  
# 3  spots_BC30004_C1.csv.gz  BC30004_C1_Coords.tsv.gz  
# 4  spots_BC42334_C1.csv.gz  BC42334_C1_Coords.tsv.gz 
    

<class 'pandas.core.series.Series'>
type                                     HCC
patient                              BC30005
replicate                                 C1
count_matrix        BC30005_C1_stdata.tsv.gz
histology_image            HE_BC30005_C1.tif
spot_coordinates     spots_BC30005_C1.csv.gz
tumor_annotation    BC30005_C1_Coords.tsv.gz
Name: 0, dtype: object
<bound method NDFrame.head of    type  patient replicate              count_matrix    histology_image  \
0   HCC  BC30001        C1  BC30001_C1_stdata.tsv.gz  HE_BC30001_C1.tif   
1   HCC  BC30002        C1  BC30002_C1_stdata.tsv.gz  HE_BC30002_C1.tif   
2   HCC  BC30003        C1  BC30003_C1_stdata.tsv.gz  HE_BC30003_C1.tif   
3   HCC  BC30004        C1  BC30004_C1_stdata.tsv.gz  HE_BC30004_C1.tif   
4   NCC  BC42334        C1  BC42334_C1_stdata.tsv.gz  HE_BC42334_C1.tif   
5   NCC  BC42740        C1  BC42740_C1_stdata.tsv.gz  HE_BC42740_C1.tif   
6   NCC  BC43740        C1  BC43740_C1_stdata.tsv.gz  HE_BC43740_C1.tif

In [18]:
dummy_labels = [{"label": "BC30005", "x_coords" : 0, "y_coords" : 0, "x_pixel_coords" : 128, "y_pixel_coords" : 128},
                {"label": "BC30005", "x_coords" : 0, "y_coords" : 1, "x_pixel_coords" : 128, "y_pixel_coords" : 384}]


In [35]:
%cd dummy/
!rm ../../ST-Net/data/hist2tscript/spots_BC30005_C1.csv.gz
!cp spots_BC30005_C1_ft.csv ../../ST-Net/data/hist2tscript/spots_BC30005_C1.csv
!gzip ../../ST-Net/data/hist2tscript/spots_BC30005_C1.csv


!rm ../../ST-Net/data/hist2tscript/BC30005_C1_stdata.tsv.gz
!cp BC30005_C1_stdata_ft.tsv ../../ST-Net/data/hist2tscript/BC30005_C1_stdata.tsv
!gzip ../../ST-Net/data/hist2tscript/BC30005_C1_stdata.tsv

!rm ../../ST-Net/data/hist2tscript/BC30005_C1_Coords.tsv.gz
!cp BC30005_C1_Coords_ft.tsv ../../ST-Net/data/hist2tscript/BC30005_C1_Coords.tsv
!gzip ../../ST-Net/data/hist2tscript/BC30005_C1_Coords.tsv

!cp metadata.csv ../../ST-Net/data/hist2tscript/metadata.csv
print("done")
%cd ..

/home/sam/Desktop/astar/TCGA_test/dummy
done
/home/sam/Desktop/astar/TCGA_test


In [36]:
!pwd

/home/sam/Desktop/astar/TCGA_test


In [21]:
import time
import os
import openslide
import pandas as pd 
img_dir = "./0166427c-15c9-4b49-954c-eb3545e5699e"

start_pixel = [0,0]
orig_window = 296

def tile_images(img_dir, start_pixel, save_root, orig_window):
    start = time.time()
    i = 4
    data_list = [] 
    data_dict = {}
    level = 1
    pixel = (start_pixel[0] + orig_window//2, start_pixel[1] + orig_window//2)
    for img in os.listdir(img_dir):
        if img.endswith(".svs"):
            i+=1
            slide = openslide.open_slide(os.path.join(img_dir, img))
            dims = slide.level_dimensions[level]
            col, row = 0, 0 
            max_col, max_row = dims[0]//orig_window, dims[1]//orig_window
            
            data_path = os.path.join(save_root, f"HE_BC{30000+i}_C1")
            try:
               os.makedirs(data_path)
            except FileExistsError:
               pass
            counter = 0
            total_count = max_col * max_row 
#             max_row, max_col = 2,2
            while max_row >= row:
                while max_col >= col:
#                     print(dims)
#                     print(slide.level_count)
                    x_pixel_coords = pixel[0]+ orig_window * col
                    y_pixel_coords = pixel[1] + orig_window * row
#                     X = slide.read_region((x_pixel_coords - orig_window//2, y_pixel_coords - orig_window//2), 1, (orig_window,orig_window))
            #         print(X)
#                     X = slide.read_region((pixel[0] - orig_window // 2, pixel[1] - orig_window // 2), level, (orig_window, orig_window))
                    X = slide.read_region(((pixel[0] - orig_window // 2), (pixel[1] - orig_window // 2)), level, (orig_window, orig_window))

                    X = X.convert("RGB")
                    X.save(os.path.join(data_path,f"BC{30000+i}_{col}_{row}.tif"))
#                     display(X)
#                     print(pixel)
                    data_dict = {"label": f"BC{30000+i}", "x_coords" : col, "y_coords" : row, "x_pixel_coords" : x_pixel_coords, "y_pixel_coords" : y_pixel_coords}
                    data_list.append(data_dict)
                    col += 1
                    counter +=1
                    print(f"{counter} out of {total_count}")
#                     print(data_list)
                col = 0
                row += 1 
                pixel = pixel[0], pixel[1]+ orig_window
    df = pd.DataFrame(data_list)
    df.to_csv(os.path.join(save_root, "labels.csv"))
    print("done")         
    end = time.time()
    print(end-start, "seconds")

       
                
print(tile_images(img_dir, start_pixel, "/home/sam/Desktop/astar/TCGA_test/tiled_data", orig_window))
                
'''
osh  = openslide.OpenSlide("0166427c-15c9-4b49-954c-eb3545e5699e/TCGA-BC-A217-01Z-00-DX1.E15D9B32-F809-40D8-846B-2334447B80C0.svs")
print(osh.level_count)
'''


1 out of 8001
2 out of 8001
3 out of 8001
4 out of 8001
5 out of 8001
6 out of 8001
7 out of 8001
8 out of 8001
9 out of 8001
10 out of 8001
11 out of 8001
12 out of 8001
13 out of 8001
14 out of 8001
15 out of 8001
16 out of 8001
17 out of 8001
18 out of 8001
19 out of 8001
20 out of 8001
21 out of 8001
22 out of 8001
23 out of 8001
24 out of 8001
25 out of 8001
26 out of 8001
27 out of 8001
28 out of 8001
29 out of 8001
30 out of 8001
31 out of 8001
32 out of 8001
33 out of 8001
34 out of 8001
35 out of 8001
36 out of 8001
37 out of 8001
38 out of 8001
39 out of 8001
40 out of 8001
41 out of 8001
42 out of 8001
43 out of 8001
44 out of 8001
45 out of 8001
46 out of 8001
47 out of 8001
48 out of 8001
49 out of 8001
50 out of 8001
51 out of 8001
52 out of 8001
53 out of 8001
54 out of 8001
55 out of 8001
56 out of 8001
57 out of 8001
58 out of 8001
59 out of 8001
60 out of 8001
61 out of 8001
62 out of 8001
63 out of 8001
64 out of 8001
65 out of 8001
66 out of 8001
67 out of 8001
68 o

542 out of 8001
543 out of 8001
544 out of 8001
545 out of 8001
546 out of 8001
547 out of 8001
548 out of 8001
549 out of 8001
550 out of 8001
551 out of 8001
552 out of 8001
553 out of 8001
554 out of 8001
555 out of 8001
556 out of 8001
557 out of 8001
558 out of 8001
559 out of 8001
560 out of 8001
561 out of 8001
562 out of 8001
563 out of 8001
564 out of 8001
565 out of 8001
566 out of 8001
567 out of 8001
568 out of 8001
569 out of 8001
570 out of 8001
571 out of 8001
572 out of 8001
573 out of 8001
574 out of 8001
575 out of 8001
576 out of 8001
577 out of 8001
578 out of 8001
579 out of 8001
580 out of 8001
581 out of 8001
582 out of 8001
583 out of 8001
584 out of 8001
585 out of 8001
586 out of 8001
587 out of 8001
588 out of 8001
589 out of 8001
590 out of 8001
591 out of 8001
592 out of 8001
593 out of 8001
594 out of 8001
595 out of 8001
596 out of 8001
597 out of 8001
598 out of 8001
599 out of 8001
600 out of 8001
601 out of 8001
602 out of 8001
603 out of 8001
604 out 

1069 out of 8001
1070 out of 8001
1071 out of 8001
1072 out of 8001
1073 out of 8001
1074 out of 8001
1075 out of 8001
1076 out of 8001
1077 out of 8001
1078 out of 8001
1079 out of 8001
1080 out of 8001
1081 out of 8001
1082 out of 8001
1083 out of 8001
1084 out of 8001
1085 out of 8001
1086 out of 8001
1087 out of 8001
1088 out of 8001
1089 out of 8001
1090 out of 8001
1091 out of 8001
1092 out of 8001
1093 out of 8001
1094 out of 8001
1095 out of 8001
1096 out of 8001
1097 out of 8001
1098 out of 8001
1099 out of 8001
1100 out of 8001
1101 out of 8001
1102 out of 8001
1103 out of 8001
1104 out of 8001
1105 out of 8001
1106 out of 8001
1107 out of 8001
1108 out of 8001
1109 out of 8001
1110 out of 8001
1111 out of 8001
1112 out of 8001
1113 out of 8001
1114 out of 8001
1115 out of 8001
1116 out of 8001
1117 out of 8001
1118 out of 8001
1119 out of 8001
1120 out of 8001
1121 out of 8001
1122 out of 8001
1123 out of 8001
1124 out of 8001
1125 out of 8001
1126 out of 8001
1127 out of 80

1561 out of 8001
1562 out of 8001
1563 out of 8001
1564 out of 8001
1565 out of 8001
1566 out of 8001
1567 out of 8001
1568 out of 8001
1569 out of 8001
1570 out of 8001
1571 out of 8001
1572 out of 8001
1573 out of 8001
1574 out of 8001
1575 out of 8001
1576 out of 8001
1577 out of 8001
1578 out of 8001
1579 out of 8001
1580 out of 8001
1581 out of 8001
1582 out of 8001
1583 out of 8001
1584 out of 8001
1585 out of 8001
1586 out of 8001
1587 out of 8001
1588 out of 8001
1589 out of 8001
1590 out of 8001
1591 out of 8001
1592 out of 8001
1593 out of 8001
1594 out of 8001
1595 out of 8001
1596 out of 8001
1597 out of 8001
1598 out of 8001
1599 out of 8001
1600 out of 8001
1601 out of 8001
1602 out of 8001
1603 out of 8001
1604 out of 8001
1605 out of 8001
1606 out of 8001
1607 out of 8001
1608 out of 8001
1609 out of 8001
1610 out of 8001
1611 out of 8001
1612 out of 8001
1613 out of 8001
1614 out of 8001
1615 out of 8001
1616 out of 8001
1617 out of 8001
1618 out of 8001
1619 out of 80

2050 out of 8001
2051 out of 8001
2052 out of 8001
2053 out of 8001
2054 out of 8001
2055 out of 8001
2056 out of 8001
2057 out of 8001
2058 out of 8001
2059 out of 8001
2060 out of 8001
2061 out of 8001
2062 out of 8001
2063 out of 8001
2064 out of 8001
2065 out of 8001
2066 out of 8001
2067 out of 8001
2068 out of 8001
2069 out of 8001
2070 out of 8001
2071 out of 8001
2072 out of 8001
2073 out of 8001
2074 out of 8001
2075 out of 8001
2076 out of 8001
2077 out of 8001
2078 out of 8001
2079 out of 8001
2080 out of 8001
2081 out of 8001
2082 out of 8001
2083 out of 8001
2084 out of 8001
2085 out of 8001
2086 out of 8001
2087 out of 8001
2088 out of 8001
2089 out of 8001
2090 out of 8001
2091 out of 8001
2092 out of 8001
2093 out of 8001
2094 out of 8001
2095 out of 8001
2096 out of 8001
2097 out of 8001
2098 out of 8001
2099 out of 8001
2100 out of 8001
2101 out of 8001
2102 out of 8001
2103 out of 8001
2104 out of 8001
2105 out of 8001
2106 out of 8001
2107 out of 8001
2108 out of 80

...

6472 out of 8001
6473 out of 8001
6474 out of 8001
6475 out of 8001
6476 out of 8001
6477 out of 8001
6478 out of 8001
6479 out of 8001
6480 out of 8001
6481 out of 8001
6482 out of 8001
6483 out of 8001
6484 out of 8001
6485 out of 8001
6486 out of 8001
6487 out of 8001
6488 out of 8001
6489 out of 8001
6490 out of 8001
6491 out of 8001
6492 out of 8001
6493 out of 8001
6494 out of 8001
6495 out of 8001
6496 out of 8001
6497 out of 8001
6498 out of 8001
6499 out of 8001
6500 out of 8001
6501 out of 8001
6502 out of 8001
6503 out of 8001
6504 out of 8001
6505 out of 8001
6506 out of 8001
6507 out of 8001
6508 out of 8001
6509 out of 8001
6510 out of 8001
6511 out of 8001
6512 out of 8001
6513 out of 8001
6514 out of 8001
6515 out of 8001
6516 out of 8001
6517 out of 8001
6518 out of 8001
6519 out of 8001
6520 out of 8001
6521 out of 8001
6522 out of 8001
6523 out of 8001
6524 out of 8001
6525 out of 8001
6526 out of 8001
6527 out of 8001
6528 out of 8001
6529 out of 8001
6530 out of 80

6964 out of 8001
6965 out of 8001
6966 out of 8001
6967 out of 8001
6968 out of 8001
6969 out of 8001
6970 out of 8001
6971 out of 8001
6972 out of 8001
6973 out of 8001
6974 out of 8001
6975 out of 8001
6976 out of 8001
6977 out of 8001
6978 out of 8001
6979 out of 8001
6980 out of 8001
6981 out of 8001
6982 out of 8001
6983 out of 8001
6984 out of 8001
6985 out of 8001
6986 out of 8001
6987 out of 8001
6988 out of 8001
6989 out of 8001
6990 out of 8001
6991 out of 8001
6992 out of 8001
6993 out of 8001
6994 out of 8001
6995 out of 8001
6996 out of 8001
6997 out of 8001
6998 out of 8001
6999 out of 8001
7000 out of 8001
7001 out of 8001
7002 out of 8001
7003 out of 8001
7004 out of 8001
7005 out of 8001
7006 out of 8001
7007 out of 8001
7008 out of 8001
7009 out of 8001
7010 out of 8001
7011 out of 8001
7012 out of 8001
7013 out of 8001
7014 out of 8001
7015 out of 8001
7016 out of 8001
7017 out of 8001
7018 out of 8001
7019 out of 8001
7020 out of 8001
7021 out of 8001
7022 out of 80

7456 out of 8001
7457 out of 8001
7458 out of 8001
7459 out of 8001
7460 out of 8001
7461 out of 8001
7462 out of 8001
7463 out of 8001
7464 out of 8001
7465 out of 8001
7466 out of 8001
7467 out of 8001
7468 out of 8001
7469 out of 8001
7470 out of 8001
7471 out of 8001
7472 out of 8001
7473 out of 8001
7474 out of 8001
7475 out of 8001
7476 out of 8001
7477 out of 8001
7478 out of 8001
7479 out of 8001
7480 out of 8001
7481 out of 8001
7482 out of 8001
7483 out of 8001
7484 out of 8001
7485 out of 8001
7486 out of 8001
7487 out of 8001
7488 out of 8001
7489 out of 8001
7490 out of 8001
7491 out of 8001
7492 out of 8001
7493 out of 8001
7494 out of 8001
7495 out of 8001
7496 out of 8001
7497 out of 8001
7498 out of 8001
7499 out of 8001
7500 out of 8001
7501 out of 8001
7502 out of 8001
7503 out of 8001
7504 out of 8001
7505 out of 8001
7506 out of 8001
7507 out of 8001
7508 out of 8001
7509 out of 8001
7510 out of 8001
7511 out of 8001
7512 out of 8001
7513 out of 8001
7514 out of 80

7952 out of 8001
7953 out of 8001
7954 out of 8001
7955 out of 8001
7956 out of 8001
7957 out of 8001
7958 out of 8001
7959 out of 8001
7960 out of 8001
7961 out of 8001
7962 out of 8001
7963 out of 8001
7964 out of 8001
7965 out of 8001
7966 out of 8001
7967 out of 8001
7968 out of 8001
7969 out of 8001
7970 out of 8001
7971 out of 8001
7972 out of 8001
7973 out of 8001
7974 out of 8001
7975 out of 8001
7976 out of 8001
7977 out of 8001
7978 out of 8001
7979 out of 8001
7980 out of 8001
7981 out of 8001
7982 out of 8001
7983 out of 8001
7984 out of 8001
7985 out of 8001
7986 out of 8001
7987 out of 8001
7988 out of 8001
7989 out of 8001
7990 out of 8001
7991 out of 8001
7992 out of 8001
7993 out of 8001
7994 out of 8001
7995 out of 8001
7996 out of 8001
7997 out of 8001
7998 out of 8001
7999 out of 8001
8000 out of 8001
8001 out of 8001
8002 out of 8001
8003 out of 8001
8004 out of 8001
8005 out of 8001
8006 out of 8001
8007 out of 8001
8008 out of 8001
8009 out of 8001
8010 out of 80

'\nosh  = openslide.OpenSlide("0166427c-15c9-4b49-954c-eb3545e5699e/TCGA-BC-A217-01Z-00-DX1.E15D9B32-F809-40D8-846B-2334447B80C0.svs")\nprint(osh.level_count)\n'

In [5]:
import pandas as pd
import openslide
import os
import numpy as np
# from PIL import Image
from IPython.display import display

In [7]:
#get dimensions for the file
from PIL import Image
# Image.MAX_IMAGE_SIZE = None
img_dir = "./0166427c-15c9-4b49-954c-eb3545e5699e"
save_root = "/home/sam/Desktop/astar/TCGA_test"



#start at top left 
pixel = (0,0)
window = 256
midpoint = (pixel[0]+ window//2, pixel[1] + window//2)

x_coord = 0 
y_coord = 0

level = 1

i = 4 


for img in os.listdir(img_dir):
    if img.endswith(".svs"):
        i+=1
        slide = openslide.open_slide(os.path.join(img_dir, img))
        print(type(slide))
        dims = slide.level_dimensions[level]
        print(dims)
        print(slide.level_count) 
        
        X = slide.read_region((0,0), level, dims)
#         img_RGB = np.transpose(np.array(slide.read_region((0, 0),
#                                level,
#                                slide.level_dimensions[level]).convert('RGB')),
#                                axes=[1, 0, 2])

#         X = X.convert("RGB")
#         data_path = os.path.join(save_root, f"HE_BC{30000+i}_C1")
        X.save(os.path.join(save_root,f"HE_BC{30000+i}_C1.tif"))

        
        
#         print(slide.properties)
#         print(slide.properties[PROPERTY_NAME_OBJECTIVE_POWER])
#         slide_thumb_600 = slide.get_thumbnail(size = (600,600))
#         display(slide_thumb_600)

    

<class 'openslide.OpenSlide'>
(37841, 18751)
4


In [ ]:
import jupyter_core.paths as paths
print(paths.jupyter_data_dir())


In [ ]:
# import CV2
# def max99(im):
#     l=im.flatten()
#     return l[list(l).index(sorted(l)[round(0.99*len(l))])]

# imInput = skimage.io.imread(inputImageFile)[:,:,:3]
# thr=cv2.cvtColor(imInput,cv2.COLOR_RGB2GRAY)
# r,thr=cv2.threshold(thr,max99(imInput),255,cv2.THRESH_BINARY)        
# thr=cv2.bitwise_not(thr)

In [ ]:
# #!/usr/bin/env python
# #
# # deepzoom_server - Example web application for serving whole-slide images
# #
# # Copyright (c) 2010-2015 Carnegie Mellon University
# #
# # This library is free software; you can redistribute it and/or modify it
# # under the terms of version 2.1 of the GNU Lesser General Public License
# # as published by the Free Software Foundation.
# #
# # This library is distributed in the hope that it will be useful, but
# # WITHOUT ANY WARRANTY; without even the implied warranty of MERCHANTABILITY
# # or FITNESS FOR A PARTICULAR PURPOSE.  See the GNU Lesser General Public
# # License for more details.
# #
# # You should have received a copy of the GNU Lesser General Public License
# # along with this library; if not, write to the Free Software Foundation,
# # Inc., 51 Franklin Street, Fifth Floor, Boston, MA 02110-1301 USA.
# #

# from io import BytesIO
# from optparse import OptionParser
# import os
# import re
# from unicodedata import normalize

# from flask import Flask, abort, make_response, render_template, url_for

# if os.name == 'nt':
#     _dll_path = os.getenv('OPENSLIDE_PATH')
#     if _dll_path is not None:
#         if hasattr(os, 'add_dll_directory'):
#             # Python >= 3.8
#             with os.add_dll_directory(_dll_path):
#                 import openslide
#         else:
#             # Python < 3.8
#             _orig_path = os.environ.get('PATH', '')
#             os.environ['PATH'] = _orig_path + ';' + _dll_path
#             import openslide

#             os.environ['PATH'] = _orig_path
# else:
#     import openslide

# from openslide import ImageSlide, open_slide
# from openslide.deepzoom import DeepZoomGenerator

# SLIDE_NAME = 'slide'


# def create_app(config=None, config_file=None):
#     # Create and configure app
#     app = Flask(__name__)
#     app.config.from_mapping(
#         DEEPZOOM_SLIDE=None,
#         DEEPZOOM_FORMAT='jpeg',
#         DEEPZOOM_TILE_SIZE=254,
#         DEEPZOOM_OVERLAP=1,
#         DEEPZOOM_LIMIT_BOUNDS=True,
#         DEEPZOOM_TILE_QUALITY=75,
#     )
#     app.config.from_envvar('DEEPZOOM_TILER_SETTINGS', silent=True)
#     if config_file is not None:
#         app.config.from_pyfile(config_file)
#     if config is not None:
#         app.config.from_mapping(config)

#     # Open slide
#     slidefile = app.config['DEEPZOOM_SLIDE']
#     if slidefile is None:
#         raise ValueError('No slide file specified')
#     config_map = {
#         'DEEPZOOM_TILE_SIZE': 'tile_size',
#         'DEEPZOOM_OVERLAP': 'overlap',
#         'DEEPZOOM_LIMIT_BOUNDS': 'limit_bounds',
#     }
#     opts = {v: app.config[k] for k, v in config_map.items()}
#     slide = open_slide(slidefile)
#     app.slides = {SLIDE_NAME: DeepZoomGenerator(slide, **opts)}
#     app.associated_images = []
#     app.slide_properties = slide.properties
#     for name, image in slide.associated_images.items():
#         app.associated_images.append(name)
#         slug = slugify(name)
#         app.slides[slug] = DeepZoomGenerator(ImageSlide(image), **opts)
#     try:
#         mpp_x = slide.properties[openslide.PROPERTY_NAME_MPP_X]
#         mpp_y = slide.properties[openslide.PROPERTY_NAME_MPP_Y]
#         app.slide_mpp = (float(mpp_x) + float(mpp_y)) / 2
#     except (KeyError, ValueError):
#         app.slide_mpp = 0

#     # Set up routes
#     @app.route('/')
#     def index():
#         slide_url = url_for('dzi', slug=SLIDE_NAME)
#         associated_urls = {
#             name: url_for('dzi', slug=slugify(name)) for name in app.associated_images
#         }
#         return render_template(
#             'slide-multipane.html',
#             slide_url=slide_url,
#             associated=associated_urls,
#             properties=app.slide_properties,
#             slide_mpp=app.slide_mpp,
#         )

#     @app.route('/<slug>.dzi')
#     def dzi(slug):
#         format = app.config['DEEPZOOM_FORMAT']
#         try:
#             resp = make_response(app.slides[slug].get_dzi(format))
#             resp.mimetype = 'application/xml'
#             return resp
#         except KeyError:
#             # Unknown slug
#             abort(404)

#     @app.route('/<slug>_files/<int:level>/<int:col>_<int:row>.<format>')
#     def tile(slug, level, col, row, format):
#         format = format.lower()
#         if format != 'jpeg' and format != 'png':
#             # Not supported by Deep Zoom
#             abort(404)
#         try:
#             tile = app.slides[slug].get_tile(level, (col, row))
#         except KeyError:
#             # Unknown slug
#             abort(404)
#         except ValueError:
#             # Invalid level or coordinates
#             abort(404)
#         buf = BytesIO()
#         tile.save(buf, format, quality=app.config['DEEPZOOM_TILE_QUALITY'])
#         resp = make_response(buf.getvalue())
#         resp.mimetype = 'image/%s' % format
#         return resp

#     return app


# def slugify(text):
#     text = normalize('NFKD', text.lower()).encode('ascii', 'ignore').decode()
#     return re.sub('[^a-z0-9]+', '-', text)


# if __name__ == '__main__':
#     parser = OptionParser(usage='Usage: %prog [options] [slide]')
#     parser.add_option(
#         '-B',
#         '--ignore-bounds',
#         dest='DEEPZOOM_LIMIT_BOUNDS',
#         default=True,
#         action='store_false',
#         help='display entire scan area',
#     )
#     parser.add_option(
#         '-c', '--config', metavar='FILE', dest='config', help='config file'
#     )
#     parser.add_option(
#         '-d',
#         '--debug',
#         dest='DEBUG',
#         action='store_true',
#         help='run in debugging mode (insecure)',
#     )
#     parser.add_option(
#         '-e',
#         '--overlap',
#         metavar='PIXELS',
#         dest='DEEPZOOM_OVERLAP',
#         type='int',
#         help='overlap of adjacent tiles [1]',
#     )
#     parser.add_option(
#         '-f',
#         '--format',
#         metavar='{jpeg|png}',
#         dest='DEEPZOOM_FORMAT',
#         help='image format for tiles [jpeg]',
#     )
#     parser.add_option(
#         '-l',
#         '--listen',
#         metavar='ADDRESS',
#         dest='host',
#         default='127.0.0.1',
#         help='address to listen on [127.0.0.1]',
#     )
#     parser.add_option(
#         '-p',
#         '--port',
#         metavar='PORT',
#         dest='port',
#         type='int',
#         default=5000,
#         help='port to listen on [5000]',
#     )
#     parser.add_option(
#         '-Q',
#         '--quality',
#         metavar='QUALITY',
#         dest='DEEPZOOM_TILE_QUALITY',
#         type='int',
#         help='JPEG compression quality [75]',
#     )
#     parser.add_option(
#         '-s',
#         '--size',
#         metavar='PIXELS',
#         dest='DEEPZOOM_TILE_SIZE',
#         type='int',
#         help='tile size [254]',
#     )

#     (opts, args) = parser.parse_args()
#     config = {}
#     config_file = opts.config
#     # Set only those settings specified on the command line
#     for k in dir(opts):
#         v = getattr(opts, k)
#         if not k.startswith('_') and v is not None:
#             config[k] = v
#     # Set slide file if specified
#     try:
#         config['DEEPZOOM_SLIDE'] = args[0]
#     except IndexError:
#         pass
#     app = create_app(config, config_file)

#     app.run(host=opts.host, port=opts.port, threaded=True)

In [37]:
!pwd
!cd processed/grid

/home/sam/Desktop/astar/TCGA_test


In [53]:
!ls processed/HE_BC3005/


tile_0_level0_2072-37888-2368-38184.tif
tile_10000_level0_21608-18944-21904-19240.tif
tile_10001_level0_21608-19240-21904-19536.tif
tile_10002_level0_21608-19536-21904-19832.tif
tile_10003_level0_21608-19832-21904-20128.tif
tile_10004_level0_21608-20128-21904-20424.tif
tile_10005_level0_21608-20424-21904-20720.tif
tile_10006_level0_21608-20720-21904-21016.tif
tile_10007_level0_21608-21016-21904-21312.tif
tile_10008_level0_21608-21312-21904-21608.tif
tile_10009_level0_21608-21608-21904-21904.tif
tile_1000_level0_6512-33744-6808-34040.tif
tile_10010_level0_21608-21904-21904-22200.tif
tile_10011_level0_21608-22200-21904-22496.tif
tile_10012_level0_21608-22496-21904-22792.tif
tile_10013_level0_21608-22792-21904-23088.tif
tile_10014_level0_21608-23088-21904-23384.tif
tile_10015_level0_21608-23384-21904-23680.tif
tile_10016_level0_21608-23680-21904-23976.tif
tile_10017_level0_21608-23976-21904-24272.tif
tile_10018_level0_21608-24272-21904-24568.tif
tile_10019_level0_21608-24568-21904-24864.t

tile_16486_level0_30192-8288-30488-8584.tif
tile_16487_level0_30192-8584-30488-8880.tif
tile_16488_level0_30192-8880-30488-9176.tif
tile_16489_level0_30192-9176-30488-9472.tif
tile_1648_level0_8288-26048-8584-26344.tif
tile_16490_level0_30192-9472-30488-9768.tif
tile_16491_level0_30192-9768-30488-10064.tif
tile_16492_level0_30192-10064-30488-10360.tif
tile_16493_level0_30192-10360-30488-10656.tif
tile_16494_level0_30192-10656-30488-10952.tif
tile_16495_level0_30192-10952-30488-11248.tif
tile_16496_level0_30192-11248-30488-11544.tif
tile_16497_level0_30192-11544-30488-11840.tif
tile_16498_level0_30192-11840-30488-12136.tif
tile_16499_level0_30192-12136-30488-12432.tif
tile_1649_level0_8288-26344-8584-26640.tif
tile_164_level0_3256-44104-3552-44400.tif
tile_16500_level0_30192-12432-30488-12728.tif
tile_16501_level0_30192-12728-30488-13024.tif
tile_16502_level0_30192-13024-30488-13320.tif
tile_16503_level0_30192-13320-30488-13616.tif
tile_16504_level0_30192-13616-30488-13912.tif
tile_1650

tile_2388_level0_9768-34632-10064-34928.tif
tile_23890_level0_39368-67488-39664-67784.tif
tile_23891_level0_39368-67784-39664-68080.tif
tile_23892_level0_39368-68080-39664-68376.tif
tile_23893_level0_39368-68376-39664-68672.tif
tile_23894_level0_39368-68672-39664-68968.tif
tile_23895_level0_39368-68968-39664-69264.tif
tile_23896_level0_39368-69264-39664-69560.tif
tile_23897_level0_39368-69560-39664-69856.tif
tile_23898_level0_39368-69856-39664-70152.tif
tile_23899_level0_39368-70152-39664-70448.tif
tile_2389_level0_9768-34928-10064-35224.tif
tile_238_level0_3848-33448-4144-33744.tif
tile_23900_level0_39664-1184-39960-1480.tif
tile_23901_level0_39664-1480-39960-1776.tif
tile_23902_level0_39664-1776-39960-2072.tif
tile_23903_level0_39664-2072-39960-2368.tif
tile_23904_level0_39664-2368-39960-2664.tif
tile_23905_level0_39664-2664-39960-2960.tif
tile_23906_level0_39664-2960-39960-3256.tif
tile_23907_level0_39664-3256-39960-3552.tif
tile_23908_level0_39664-3552-39960-3848.tif
tile_23909_lev

tile_34181_level0_52984-7992-53280-8288.tif
tile_34182_level0_52984-8288-53280-8584.tif
tile_34183_level0_52984-8584-53280-8880.tif
tile_34184_level0_52984-8880-53280-9176.tif
tile_34185_level0_52984-9176-53280-9472.tif
tile_34186_level0_52984-9472-53280-9768.tif
tile_34187_level0_52984-9768-53280-10064.tif
tile_34188_level0_52984-10064-53280-10360.tif
tile_34189_level0_52984-10360-53280-10656.tif
tile_3418_level0_11544-50320-11840-50616.tif
tile_34190_level0_52984-10656-53280-10952.tif
tile_34191_level0_52984-10952-53280-11248.tif
tile_34192_level0_52984-11248-53280-11544.tif
tile_34193_level0_52984-11544-53280-11840.tif
tile_34194_level0_52984-11840-53280-12136.tif
tile_34195_level0_52984-12136-53280-12432.tif
tile_34196_level0_52984-12432-53280-12728.tif
tile_34197_level0_52984-12728-53280-13024.tif
tile_34198_level0_52984-13024-53280-13320.tif
tile_34199_level0_52984-13320-53280-13616.tif
tile_3419_level0_11544-50616-11840-50912.tif
tile_341_level0_4144-45880-4440-46176.tif
tile_34

tile_44418_level0_101824-39072-102120-39368.tif
tile_44419_level0_101824-39368-102120-39664.tif
tile_4441_level0_13320-32264-13616-32560.tif
tile_44420_level0_101824-39664-102120-39960.tif
tile_44421_level0_101824-39960-102120-40256.tif
tile_44422_level0_101824-40256-102120-40552.tif
tile_44423_level0_101824-40552-102120-40848.tif
tile_44424_level0_101824-40848-102120-41144.tif
tile_44425_level0_101824-41144-102120-41440.tif
tile_44426_level0_101824-41440-102120-41736.tif
tile_44427_level0_101824-41736-102120-42032.tif
tile_44428_level0_101824-42032-102120-42328.tif
tile_44429_level0_101824-42328-102120-42624.tif
tile_4442_level0_13320-32560-13616-32856.tif
tile_44430_level0_101824-42624-102120-42920.tif
tile_44431_level0_101824-42920-102120-43216.tif
tile_44432_level0_101824-43216-102120-43512.tif
tile_44433_level0_101824-43512-102120-43808.tif
tile_44434_level0_101824-43808-102120-44104.tif
tile_44435_level0_101824-44104-102120-44400.tif
tile_44436_level0_101824-44400-102120-44696.ti

tile_54492_level0_116624-8880-116920-9176.tif
tile_54493_level0_116624-9176-116920-9472.tif
tile_54494_level0_116624-9472-116920-9768.tif
tile_54495_level0_116624-9768-116920-10064.tif
tile_54496_level0_116624-10064-116920-10360.tif
tile_54497_level0_116624-10360-116920-10656.tif
tile_54498_level0_116624-10656-116920-10952.tif
tile_54499_level0_116624-10952-116920-11248.tif
tile_5449_level0_14800-61568-15096-61864.tif
tile_544_level0_5032-40256-5328-40552.tif
tile_54500_level0_116624-11248-116920-11544.tif
tile_54501_level0_116624-11544-116920-11840.tif
tile_54502_level0_116624-11840-116920-12136.tif
tile_54503_level0_116624-12136-116920-12432.tif
tile_54504_level0_116624-12432-116920-12728.tif
tile_54505_level0_116624-12728-116920-13024.tif
tile_54506_level0_116624-13024-116920-13320.tif
tile_54507_level0_116624-13320-116920-13616.tif
tile_54508_level0_116624-13616-116920-13912.tif
tile_54509_level0_116624-13912-116920-14208.tif
tile_5450_level0_14800-61864-15096-62160.tif
tile_54510_

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [3]:
# import os
# orig_window = 296


# def tile_images(img_dir, i, orig_window):
#     data_list = [] 
#     data_dict = {}
#     new_dir = os.path.join(os.path.abspath(os.path.join(img_dir, os.pardir)),f"HE_BC{30000+i}/")
#     os.rename(img_dir, new_dir)
#     for img in os.listdir(new_dir):
#         print(img)
#         if img.endswith(".tif"):
#             info = img.split("_")
#             coord_info = info[3].split("-")
#             col = int(coord_info[0])//orig_window
#             row = int(coord_info[1])//orig_window
#             # BC30001_99_59.tif

#             data_dict = {"label": f"BC{30000+i}", "x_coords" : col, "y_coords" : row, "x_pixel_coords" : coord_info[0], "y_pixel_coords" : coord_info[1]}
#             data_list.append(data_dict)
# #             print(os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
#             os.rename(os.path.join(new_dir, img), os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
        
    
# #    tile_images("./processed/grid/", 5, 296)

tile_1519_level1_39072-17760-40256-18944.tif
tile_2085_level1_49728-62752-50913-63936.tif
tile_4410_level1_133794-62752-134978-63936.tif
tile_1928_level1_47360-14208-48544-15392.tif
tile_1112_level1_30784-26048-31968-27232.tif
tile_2787_level1_99457-28416-100641-29600.tif
tile_1803_level1_44992-4736-46176-5920.tif
tile_3775_level1_121954-3552-123138-4736.tif
tile_1266_level1_33152-67488-34336-68672.tif
tile_4595_level1_138530-9472-139714-10656.tif
tile_1299_level1_34336-36704-35520-37888.tif
tile_1767_level1_43808-31968-44992-33152.tif
tile_3483_level1_116034-5920-117218-7104.tif
tile_1231_level1_33152-26048-34336-27232.tif
tile_1416_level1_36704-35520-37888-36704.tif
tile_1873_level1_46176-17760-47360-18944.tif
tile_1502_level1_37888-67488-39072-68672.tif
tile_4260_level1_131426-24864-132610-26048.tif
tile_4855_level1_144450-5920-145634-7104.tif
tile_847_level1_24864-55648-26048-56832.tif
tile_4915_level1_145634-21312-146818-22496.tif
tile_4806_level1_143266-5920-144450-7104.tif
tile_

In [7]:
!pwd

/home/sam/Desktop/astar/TCGA_test


In [9]:
# Script for downsampling to 20x 

import os
from PIL import Image
import time
import pandas as pd

orig_window = 296


def tile_images(img_dir, i, orig_window, scale_factor):
    start = time.time()
    data_list = [] 
    data_dict = {}
    new_dir = os.path.join(os.path.abspath(os.path.join(img_dir, os.pardir)),f"HE_BC{30000+i}/")
    try:
        os.mkdir(new_dir)
    except FileExistsError:
        pass
    
    for img in os.listdir(img_dir):
        print(img)
        if img.endswith(".tif"):
            info = img.split("_")
            coord_info = info[3].split("-")
            col = int(coord_info[0])//(orig_window*scale_factor)
            row = int(coord_info[1])//(orig_window*scale_factor)
            # BC30001_99_59.tif

            data_dict = {"label": f"BC{30000+i}", "x_coords" : col, "y_coords" : row, "x_pixel_coords" : int(coord_info[0])//scale_factor, "y_pixel_coords" : int(coord_info[1])//scale_factor}
            data_list.append(data_dict)
#             print(os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
            
            im = Image.open(os.path.join(img_dir, img)).resize((orig_window, orig_window), resample=Image.BICUBIC)
            im.save(os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
#             os.rename(os.path.join(new_dir, img), os.path.join(new_dir, f"{data_dict['label']}_{col}_{row}.tif"))
    df = pd.DataFrame(data_list)
    df.to_csv(os.path.join(img_dir, "labels.csv"))
    print("done")         
    end = time.time()
    print(end-start, "seconds")

    

tile_images("./processed/grid/", 5, 296, 2)

tile_230_level0_5920-46768-6512-47360.tif
tile_5886_level0_39072-4144-39664-4736.tif
tile_491_level0_8880-29600-9472-30192.tif
tile_18977_level0_143856-17168-144448-17760.tif
tile_6688_level0_42624-65712-43216-66304.tif
tile_6253_level0_40848-14800-41440-15392.tif
tile_12698_level0_110704-46176-111296-46768.tif
tile_6069_level0_39664-44400-40256-44992.tif
tile_16030_level0_127872-64528-128464-65120.tif
tile_1896_level0_17760-65120-18352-65712.tif
tile_17324_level0_134976-5328-135568-5920.tif
tile_11016_level0_100640-23680-101232-24272.tif
tile_18260_level0_139712-21904-140304-22496.tif
tile_11233_level0_101824-56832-102416-57424.tif
tile_10992_level0_100048-55648-100640-56240.tif
tile_1793_level0_17168-63344-17760-63936.tif
tile_6863_level0_43808-34336-44400-34928.tif
tile_14131_level0_118400-42624-118992-43216.tif
tile_17756_level0_136752-55056-137344-55648.tif
tile_8381_level0_51504-45584-52096-46176.tif
tile_9517_level0_58016-49136-58608-49728.tif
tile_13113_level0_113072-37888-1136

/tmp/ipykernel_310710/2349629265.py:34: DeprecationWarning: BICUBIC is deprecated and will be removed in Pillow 10 (2023-07-01). Use Resampling.BICUBIC instead.
  im = Image.open(os.path.join(img_dir, img)).resize((orig_window, orig_window), resample=Image.BICUBIC)


tile_19345_level0_146224-8880-146816-9472.tif
tile_10705_level0_98272-22496-98864-23088.tif
tile_8205_level0_50912-7104-51504-7696.tif
tile_5974_level0_39072-56832-39664-57424.tif
tile_6462_level0_41440-69856-42032-70448.tif
tile_11918_level0_106560-23088-107152-23680.tif
tile_9927_level0_61568-42624-62160-43216.tif
tile_14283_level0_118992-62752-119584-63344.tif
tile_18864_level0_143264-8288-143856-8880.tif
tile_19547_level0_148000-14800-148592-15392.tif
tile_15395_level0_124912-32560-125504-33152.tif
tile_14611_level0_120768-50320-121360-50912.tif
tile_16736_level0_131424-71632-132016-72224.tif
tile_11358_level0_103008-29600-103600-30192.tif
tile_623_level0_10064-22496-10656-23088.tif
tile_6565_level0_42032-62160-42624-62752.tif
tile_2385_level0_20720-39664-21312-40256.tif
tile_10460_level0_95904-40848-96496-41440.tif
tile_14091_level0_118400-18944-118992-19536.tif
tile_5092_level0_34928-17168-35520-17760.tif
tile_3366_level0_26048-21904-26640-22496.tif
tile_4865_level0_33744-21312-3

tile_9549_level0_58608-11840-59200-12432.tif
tile_13341_level0_114256-42032-114848-42624.tif
tile_6625_level0_42624-28416-43216-29008.tif
tile_5166_level0_34928-60976-35520-61568.tif
tile_8313_level0_51504-4736-52096-5328.tif
tile_11834_level0_105968-32560-106560-33152.tif
tile_10379_level0_95312-26640-95904-27232.tif
tile_2469_level0_21312-22496-21904-23088.tif
tile_1287_level0_14208-46176-14800-46768.tif
tile_2620_level0_21904-43808-22496-44400.tif
tile_18524_level0_140896-50912-141488-51504.tif
tile_18939_level0_143264-52688-143856-53280.tif
tile_10131_level0_91760-38480-92352-39072.tif
tile_16549_level0_130832-29600-131424-30192.tif
tile_14660_level0_121360-10656-121952-11248.tif
tile_976_level0_12432-26640-13024-27232.tif
tile_9452_level0_58016-10656-58608-11248.tif
tile_17733_level0_136752-41440-137344-42032.tif
tile_15101_level0_123136-65712-123728-66304.tif
tile_14244_level0_118992-39664-119584-40256.tif
tile_10555_level0_96496-58608-97088-59200.tif
tile_19296_level0_145632-349

tile_11590_level0_104192-60976-104784-61568.tif
tile_17554_level0_136160-1776-136752-2368.tif
tile_8731_level0_53280-61568-53872-62160.tif
tile_1680_level0_16576-54464-17168-55056.tif
tile_3828_level0_28416-24864-29008-25456.tif
tile_14995_level0_122544-71632-123136-72224.tif
tile_2980_level0_23680-58608-24272-59200.tif
tile_10853_level0_99456-19536-100048-20128.tif
tile_16237_level0_129056-49136-129648-49728.tif
tile_16764_level0_132016-18944-132608-19536.tif
tile_9559_level0_58608-17760-59200-18352.tif
tile_14794_level0_121952-21312-122544-21904.tif
tile_3968_level0_29008-43216-29600-43808.tif
tile_5957_level0_39072-46768-39664-47360.tif
tile_1682_level0_16576-55648-17168-56240.tif
tile_18335_level0_139712-66304-140304-66896.tif
tile_12049_level0_107152-39664-107744-40256.tif
tile_5235_level0_35520-33152-36112-33744.tif
tile_18378_level0_140304-27824-140896-28416.tif
tile_18857_level0_142672-63344-143264-63936.tif
tile_3320_level0_25456-62752-26048-63344.tif
tile_14967_level0_122544-

...

tile_12543_level0_110112-18352-110704-18944.tif
tile_9750_level0_59792-26048-60384-26640.tif
tile_7111_level0_44992-43808-45584-44400.tif
tile_2083_level0_18944-50912-19536-51504.tif
tile_671_level0_10064-50912-10656-51504.tif
tile_13316_level0_114256-27232-114848-27824.tif
tile_5182_level0_35520-1184-36112-1776.tif
tile_4716_level0_33152-1776-33744-2368.tif
tile_8049_level0_49728-48544-50320-49136.tif
tile_17885_level0_137344-63936-137936-64528.tif
tile_15424_level0_124912-49728-125504-50320.tif
tile_15779_level0_126688-53872-127280-54464.tif
tile_9389_level0_57424-30784-58016-31376.tif
tile_17113_level0_133792-18944-134384-19536.tif
tile_694_level0_10064-64528-10656-65120.tif
tile_4035_level0_29600-14208-30192-14800.tif
tile_5170_level0_34928-63344-35520-63936.tif
tile_13527_level0_115440-21904-116032-22496.tif
tile_13361_level0_114256-53872-114848-54464.tif
tile_6349_level0_41440-2960-42032-3552.tif
tile_14029_level0_117808-52096-118400-52688.tif
tile_15653_level0_126096-48544-12668

tile_11855_level0_105968-44992-106560-45584.tif
tile_6791_level0_43216-59792-43808-60384.tif
tile_3369_level0_26048-24864-26640-25456.tif
tile_8783_level0_53872-29600-54464-30192.tif
tile_13422_level0_114848-24272-115440-24864.tif
tile_10998_level0_100048-59200-100640-59792.tif
tile_6142_level0_40256-18352-40848-18944.tif
tile_8528_level0_52688-4144-53280-4736.tif
tile_13159_level0_113072-65120-113664-65712.tif
tile_13468_level0_114848-51504-115440-52096.tif
tile_5610_level0_37296-47952-37888-48544.tif
tile_16632_level0_131424-10064-132016-10656.tif
tile_16501_level0_130240-68672-130832-69264.tif
tile_10054_level0_90576-32560-91168-33152.tif
tile_4079_level0_29600-41440-30192-42032.tif
tile_935_level0_11840-56240-12432-56832.tif
tile_12398_level0_108928-59200-109520-59792.tif
tile_10000_level0_88800-45584-89392-46176.tif
tile_4367_level0_31376-2368-31968-2960.tif
tile_9428_level0_57424-53872-58016-54464.tif
tile_14570_level0_120768-26048-121360-26640.tif
tile_10017_level0_89392-42032-8

tile_12593_level0_110112-48544-110704-49136.tif
tile_31_level0_2960-37296-3552-37888.tif
tile_19562_level0_148000-23680-148592-24272.tif
tile_16114_level0_128464-44992-129056-45584.tif
tile_17705_level0_136752-24272-137344-24864.tif
tile_1733_level0_17168-27232-17760-27824.tif
tile_13061_level0_113072-5328-113664-5920.tif
tile_4934_level0_33744-62160-34336-62752.tif
tile_2639_level0_21904-55648-22496-56240.tif
tile_15210_level0_123728-61568-124320-62160.tif
tile_15056_level0_123136-39072-123728-39664.tif
tile_3332_level0_26048-1776-26640-2368.tif
tile_14752_level0_121360-65120-121952-65712.tif
tile_9836_level0_60384-47952-60976-48544.tif
tile_18437_level0_140304-62752-140896-63344.tif
tile_13488_level0_114848-63344-115440-63936.tif
tile_3805_level0_28416-11248-29008-11840.tif
tile_14746_level0_121360-61568-121952-62160.tif
tile_15528_level0_125504-43216-126096-43808.tif
tile_6797_level0_43216-63344-43808-63936.tif
tile_4566_level0_31968-52096-32560-52688.tif
tile_8240_level0_50912-2782

tile_19497_level0_147408-18352-148000-18944.tif
tile_10721_level0_98272-31968-98864-32560.tif
tile_13148_level0_113072-58608-113664-59200.tif
tile_10032_level0_89984-36704-90576-37296.tif
tile_2554_level0_21904-4736-22496-5328.tif
tile_15052_level0_123136-36704-123728-37296.tif
tile_10675_level0_97680-47952-98272-48544.tif
tile_14780_level0_121952-13024-122544-13616.tif
tile_19441_level0_146816-22496-147408-23088.tif
tile_9876_level0_60976-23088-61568-23680.tif
tile_9827_level0_60384-42624-60976-43216.tif
tile_8487_level0_52096-43216-52688-43808.tif
tile_9982_level0_62752-17760-63344-18352.tif
tile_15888_level0_127280-49136-127872-49728.tif
tile_13471_level0_114848-53280-115440-53872.tif
tile_14174_level0_118400-68080-118992-68672.tif
tile_15667_level0_126096-56832-126688-57424.tif
tile_5960_level0_39072-48544-39664-49136.tif
tile_12118_level0_107744-18352-108336-18944.tif
tile_16171_level0_129056-10064-129648-10656.tif
tile_16300_level0_129648-18352-130240-18944.tif
tile_12022_level0_

done
104.75231218338013 seconds


In [ ]:
import time
import os
import openslide
import pandas as pd 
img_dir = "./0166427c-15c9-4b49-954c-eb3545e5699e"

start_pixel = [0,0]
orig_window = 256

def tile_images(img_dir, start_pixel, save_root, orig_window):
    start = time.time()
    i = 4
    data_list = [] 
    data_dict = {}
    level = 1
    pixel = (start_pixel[0] + orig_window//2, start_pixel[1] + orig_window//2)
    for img in os.listdir(img_dir):
        if img.endswith(".svs"):
            i+=1
            slide = openslide.open_slide(os.path.join(img_dir, img))
            dims = slide.level_dimensions[level]
            col, row = 0, 0 
            max_col, max_row = dims[0]//orig_window, dims[1]//orig_window
            
            data_path = os.path.join(save_root, f"HE_BC{30000+i}_C1")
            try:
               os.makedirs(data_path)
            except FileExistsError:
               pass
            counter = 0
            total_count = max_col * max_row 
#             max_row, max_col = 2,2
            while max_row >= row:
                while max_col >= col:
#                     print(dims)
#                     print(slide.level_count)
                    x_pixel_coords = pixel[0]+ orig_window * col
                    y_pixel_coords = pixel[1] + orig_window * row
#                     X = slide.read_region((x_pixel_coords - orig_window//2, y_pixel_coords - orig_window//2), 1, (orig_window,orig_window))
            #         print(X)
#                     X = slide.read_region((pixel[0] - orig_window // 2, pixel[1] - orig_window // 2), level, (orig_window, orig_window))
                    X = slide.read_region(((pixel[0] - orig_window // 2)*4, (pixel[1] - orig_window // 2)*4), level, (orig_window*4, orig_window*4))

                    X = X.convert("RGB")
                    X.save(os.path.join(data_path,f"BC{30000+i}_{col}_{row}.tif"))
#                     display(X)
#                     print(pixel)
                    data_dict = {"label": f"BC{30000+i}", "x_coords" : col, "y_coords" : row, "x_pixel_coords" : x_pixel_coords, "y_pixel_coords" : y_pixel_coords}
                    data_list.append(data_dict)
                    col += 1
                    counter +=1
                    print(f"{counter} out of {total_count}")
#                     print(data_list)
                col = 0
                row += 1 
                pixel = pixel[0], pixel[1]+ orig_window
    df = pd.DataFrame(data_list)
    df.to_csv(os.path.join(save_root, "labels.csv"))
    print("done")         
    end = time.time()
    print(end-start, "seconds")

       
                
print(tile_images(img_dir, start_pixel, "/home/sam/Desktop/astar/TCGA_test/tiled_data", orig_window))
                
'''
osh  = openslide.OpenSlide("0166427c-15c9-4b49-954c-eb3545e5699e/TCGA-BC-A217-01Z-00-DX1.E15D9B32-F809-40D8-846B-2334447B80C0.svs")
print(osh.level_count)
'''
